# Bayesian A/B-Testing

In [1]:
from typing import Dict, List, Any, Union

import numpy as np
import pandas as pd

from tqdm import tqdm

from scipy import stats
from scipy.stats import beta, gamma

# import util functions
from campaign import Campaign
from hypothesis_test import Hypothesis_AB_Test
from bayesian_test import Bayesian_AB_Test

# import visualisation / plotting
import matplotlib
matplotlib.use("Agg")
import matplotlib.pyplot as plt
import matplotlib.animation as manimation
from matplotlib.colors import rgb2hex

from graph import visualisation # conda install -n python3 -c conda-forge colorlover
import plotly
import plotly.graph_objects as go
# Init visualisation tool
plot = visualisation(renderer="vscode") # vscode | iframe for browsers

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 5000)
pd.set_option('display.width', 10000)

tqdm.pandas()

# Parameters

In [2]:
# Define Campaign Parameters
# Click-Through-Rate
CTR_A = 0.10 
CTR_B = 0.12
# Cost-per-Mill average value
CPM_MEAN_A = 11
CPM_MEAN_B = 19

# ---------------------------------------------------------
# Campaign simulation pararmeters
N_PERIODS = 2000+1
N_IMPR_PER_PERIOD = 5
SEED = 10 # both similar


# ---------------------------------------------------------
# For single evalution - number of impressons
N_IMPR = 3840 # exact # of impressions according to the hypothesis test


# Config for evaluation
config ={'metrics':
            {'ks': True, # calc. Kolmorogorov-Smirnov
             'ws': True, # calc. Wasserstein
             'jsd': False, # calc. Jensen-Shannon-Divergence
             'n_samples': 1000} # number of samples
         }

# Plotting
WIDTH_SAVE, HEIGHT_SAVE = 1200, 400

# Statistics for the single evaluation

In [3]:
# Calc. number of click after N_IMPR impressions
n_clicks_a = int(CTR_A*N_IMPR)
n_clicks_b = int(CTR_B*N_IMPR)

# Calc. cost after N_IMPR impressions
cost_a = N_IMPR*CPM_MEAN_A/1000
cost_b = N_IMPR*CPM_MEAN_B/1000

print(f'Observations:')
print(f'Impressions: {N_IMPR} - clicks A/B: {n_clicks_a} / {n_clicks_b} - cost A/B: {cost_a} / {cost_b}\n')

print(f'Average statistics (without uncertainty):')
print(f'Click-Through-Rate (CTR) A/B: {100*n_clicks_a/N_IMPR:.1f}% / {100*n_clicks_b/N_IMPR:.1f}%')
print(f'Cost-per-Click (CpC) A/B: {CPM_MEAN_A/n_clicks_a:.3f} / {CPM_MEAN_B/n_clicks_b:.3f}\n')

Observations:
Impressions: 3840 - clicks A/B: 384 / 460 - cost A/B: 42.24 / 72.96

Average statistics (without uncertainty):
Click-Through-Rate (CTR) A/B: 10.0% / 12.0%
Cost-per-Click (CpC) A/B: 0.029 / 0.041



<hr>

# Hypothesis testing - single evaluation

In [4]:
hypo = Hypothesis_AB_Test()

In [5]:
n_samples_required = hypo.calc_sample_size(CTR_A, CTR_B)
print(f'Required sample size: {n_samples_required}')

# Chi-squared test
chi2, p, dof, ex = hypo.chi2_test( n_clicks_a, N_IMPR-n_clicks_a, n_clicks_b, N_IMPR-n_clicks_b )
print(f'chi2: {chi2:.3f}')
print(f'p-value: {p:.3f}')

Required sample size: 3840
chi2: 9.610
p-value: 0.002


<hr>

# Bayesian Testing - single evaluation

In [6]:
bayes = Bayesian_AB_Test()

### Probabilistic & Loss Analysis - on static data

In [7]:
# Click-Through-Rate (CTR) - Beta distribution
# calc. parameters
alpha_a, beta_a = n_clicks_a+1, N_IMPR-n_clicks_a
alpha_b, beta_b = n_clicks_b+1, N_IMPR-n_clicks_b

# Calc. probabilities and losses
print(f'Performance metric: Click-Through-Rate (CTR)')
P = bayes.p_ba(beta(alpha_a,beta_a), beta(alpha_b,beta_b))
print(f'Probability of winner A/B, p(ratio>1) = {(1-P)*100:.1f}% / {P*100:.1f}% (sampled)')
P = bayes.p_ba_beta(alpha_a, beta_a, alpha_b, beta_b)
print(f'Probability of winner A/B, p(ratio>1) = {(1-P)*100:.1f}% / {P*100:.1f}% (analytically)')
loss_a, loss_b = bayes.loss(beta(alpha_a,beta_a), beta(alpha_b, beta_b))
print(f'Loss CTR A/B: {100*loss_a:.2f}% / {100*loss_b:.2f}% (integration)')
loss_a, loss_b = bayes.loss_beta(alpha_a, beta_a, alpha_b, beta_b)
print(f'Loss CTR A/B: {100*loss_a:.2f} / {100*loss_b:.2f} (analytically)\n')

# Cost-per-Click (CpC) - Gamma distribution
# calc. parameters
cost_a, scale_a = N_IMPR*CPM_MEAN_A/1000, 1/n_clicks_a
cost_b, scale_b = N_IMPR*CPM_MEAN_B/1000, 1/n_clicks_b
a_a, a_b = cost_a+1, cost_b+1
# Calc. probabilities and losses
print(f'Performance metric: Cost-per-Click (CpC)')
P = bayes.p_ba(gamma(a=a_a, scale=scale_a), gamma(a=a_b, scale=scale_b))
print(f'Probability of cheapest click (A/B), p(ratio>1) = {P*100:.1f}% / {(1-P)*100:.1f}% (sampled)')
loss_b, loss_a = bayes.loss(gamma(a=a_a, scale=scale_a), gamma(a=a_b, scale=scale_b))
print(f'Loss CpC A/B: {100*loss_a:.2f}% / {100*loss_b:.2f}%')

Performance metric: Click-Through-Rate (CTR)
Probability of winner A/B, p(ratio>1) = 0.3% / 99.7% (sampled)
Probability of winner A/B, p(ratio>1) = 0.3% / 99.7% (analytically)
Loss CTR A/B: 1.95% / 0.00% (integration)
Loss CTR A/B: 1.98 / -0.05 (analytically)

Performance metric: Cost-per-Click (CpC)
Probability of cheapest click (A/B), p(ratio>1) = 97.1% / 2.9% (sampled)
Loss CpC A/B: 0.03% / 4.80%


## Bayesian Metrics

### Probability of winner - Click-Through-Rate (CTR)

In [8]:
# plot CTR Beta distributions
# scan lift range
n_samples = 1_000_000
samples_a = beta.rvs(alpha_a, beta_a, size=n_samples)
samples_b = beta.rvs(alpha_b, beta_b, size=n_samples)
ratio = samples_b / samples_a
hist, bins = np.histogram(ratio, bins=1000)
id1, id2 = bins<=1, bins>1

p_ratio1 = np.sum(hist[id2[:-1]]) / n_samples
print(f'Probability of B as winner, p(ratio>1) = {p_ratio1*100:.1f}%')

# ---------------------------------------------------------------------------------------------
x2 = np.linspace(0, 0.3, 1001)
p_data = [plot.plot(x=x2, y=beta.pdf(x2, alpha_a, beta_a), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=x2, y=beta.pdf(x2, alpha_b, beta_b), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title=f'', x_label='CTR', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

p_data = [plot.plot(x=bins[id1], y=hist[id1[:-1]]/sum(hist), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=bins[id2], y=hist[id2[:-1]]/sum(hist), color=1, opacity=0.7, name='B', showlegend=True) ]
layout = plot.layout(title="", x_label='lift ratio', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

p_data = [ plot.plot(x=bins[id1], y=1-hist.cumsum()[id1[:-1]]/sum(hist), color=0, opacity=0.7, name='A', showlegend=True),
           plot.plot(x=bins[id2], y=1-hist.cumsum()[id2[:-1]]/sum(hist), color=1, opacity=0.7, name='B', showlegend=True) ]
layout = plot.layout(title="", x_label='lift ratio', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

Probability of B as winner, p(ratio>1) = 99.7%


### Probability of winner - Cost-per-Click (CpC)

In [9]:
# plot CpC Gammz distributions
# scan lift range
n_samples = 1_000_000
samples_a = gamma.rvs(a=a_a, scale=scale_a, size=n_samples)
samples_b = gamma.rvs(a=a_b, scale=scale_b, size=n_samples)
ratio = samples_b / samples_a
hist, bins = np.histogram(ratio, bins=1000)
id1, id2 = bins<=1, bins>1

p_ratio1 = 1-(np.sum(hist[id1[:-1]]) / n_samples)
print(f'Probability of A as winner, p(ratio>1) = {p_ratio1*100:.1f}%')

# ---------------------------------------------------------------------------------------------
x2 = np.linspace(0, 0.3, 1001)
p_data = [plot.plot(x=x2, y=gamma.pdf(x2, a=a_a, scale=scale_a), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=x2, y=gamma.pdf(x2, a=a_b, scale=scale_b), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title=f'', x_label='CpC', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

p_data = [plot.plot(x=bins[id1], y=hist[id1[:-1]]/sum(hist), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=bins[id2], y=hist[id2[:-1]]/sum(hist), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title="", x_label='lift ratio', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

p_data = [plot.plot(x=bins[id1], y=1-hist.cumsum()[id1[:-1]]/sum(hist), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=bins[id2], y=1-hist.cumsum()[id2[:-1]]/sum(hist), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title="", x_label='lift ratio', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

Probability of A as winner, p(ratio>1) = 97.1%


<hr>

# Simulate campaign

### Create synth. campaign data

In [10]:
# Campaign parameters
params = {'A': {'ctr': CTR_A, 'cpm':CPM_MEAN_A}, 'B': {'ctr': CTR_B, 'cpm':CPM_MEAN_B}, 'n_impr_per_period':N_IMPR_PER_PERIOD}
campaign = Campaign(params, random_seed=SEED)
df = campaign.create(n_periods=N_PERIODS)
df = campaign.agg_stats(df)

# total amount of impressions for A1, A2, B1, B2 and A & B
n_impressions_a1, n_impressions_a2 = df.n_impr_a1.sum(), df.n_impr_a2.sum()
n_impressions_b1, n_impressions_b2 = df.n_impr_b1.sum(), df.n_impr_b2.sum()
n_impressions_a, n_impressions_b = df.n_impr_a.sum(), df.n_impr_b.sum()

df.head(5)
print(f'Impressions')
print(f'A (total): {n_impressions_a} - A1/A2: {n_impressions_a1}/{n_impressions_a2}')
print(f'B (total): {n_impressions_b} - B1/B2: {n_impressions_b1}/{n_impressions_b2}')

t  n_impr_a1  n_clicks_a1   cost_a1  n_impr_a2  n_clicks_a2   cost_a2  n_impr_b1  n_clicks_b1   cost_b1  n_impr_b2  n_clicks_b2  cost_b2  n_impr_a  n_clicks_a    cost_a  n_impr_b  n_clicks_b    cost_b  acc_impr_a1  acc_cost_a1  acc_clicks_a1  acc_impr_a2  acc_cost_a2  acc_clicks_a2  acc_impr_a  acc_cost_a  acc_clicks_a  acc_impr_b1  acc_cost_b1  acc_clicks_b1  acc_impr_b2  acc_cost_b2  acc_clicks_b2  acc_impr_b  acc_cost_b  acc_clicks_b
0  0.0          0            0  0.000000          0            0  0.000000          0            0  0.000000          0            0  0.00000         0           0  0.000000         0           0  0.000000            0     0.000000              0            0     0.000000              0           0    0.000000             0            0     0.000000              0            0      0.00000              0           0    0.000000             0
1  1.0          1            0  0.010583          4            1  0.067957          2            0  0.036128          0            0  0.00000         5           1  0.078540         2           0  0.036128            1     0.010583              0            4     0.067957              1           5    0.078540             1            2     0.036128              0            0      0.00000              0           2    0.036128             0
2  2.0          4            0  0.050797          3            0  0.030781          3            0  0.055435          4            0  0.08507         7           0  0.081579         7           0  0.140506            5     0.061380              0            7     0.098739              1          12    0.160119             1            5     0.091563              0            4      0.08507              0           9    0.176634             0
3  3.0          0            0  0.000000          0            0  0.000000          1            0  0.017565          4            0  0.08833         0           0  0.000000         5           0  0.105895            5     0.061380              0            7     0.098739              1          12    0.160119             1            6     0.109129              0            8      0.17340              0          14    0.282529             0
4  4.0          1            0  0.012314          4            0  0.046021          0            0  0.000000          0            0  0.00000         5           0  0.058335         0           0  0.000000            6     0.073694              0           11     0.144759              1          17    0.218454             1            6     0.109129              0            8      0.17340              0          14    0.282529             0

Impressions
A (total): 7900 - A1/A2: 3933/3967
B (total): 7962 - B1/B2: 4031/3931


#### Visualise campaign over time

In [11]:
# Impressions / Clicks over time
p_data = [ plot.plot(x=df.t, y=df.acc_impr_a1, color=0, opacity=0.2, name='impr. A', showlegend=True),
           plot.plot(x=df.t, y=df.acc_clicks_a1, color=0, opacity=0.7, name='clicks A', showlegend=True),
           plot.plot(x=df.t, y=df.acc_impr_b1, color=1, opacity=0.2, name='impr. B', showlegend=True),
           plot.plot(x=df.t, y=df.acc_clicks_b1, color=1, opacity=0.7, name='clicks B', showlegend=True),
           ]
layout = plot.layout(title=f'Observations - impr. & clicks', x_label='time', y_label='#', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/impr_clicks.png')

# CTR / CpC over time
p_data = [ plot.plot(x=df.t, y=df.acc_clicks_a/df.acc_impr_a, color=0, opacity=0.5, name='CTR A', showlegend=True),
           plot.plot(x=df.t, y=df.acc_clicks_b/df.acc_impr_b, color=1, opacity=0.5, name='CTR B', showlegend=True),
           plot.plot(x=df.t, y=df.acc_cost_a/df.acc_clicks_a, color=0, opacity=0.5, name='CpC A', showlegend=True),
           plot.plot(x=df.t, y=df.acc_cost_b/df.acc_clicks_b, color=1, opacity=0.5, name='CpC B', showlegend=True),
           ]
layout = plot.layout(title=f'Performance - CTR & CpC', x_label='time', y_label='', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/performance.png')


### Calc. AB test stats on synth. campaign data

In [12]:
# TODO:
# - add flags to select which metrics to calc. in AA tests

# HYPO
df = hypo.transform(df)

# BAYES
df = bayes.transform(df, config)

CHI2 TEST...
- calc. chi2 A/A-test...


100%|██████████| 2002/2002 [00:00<00:00, 3087.83it/s]


- calc. chi2 A/B-test...


100%|██████████| 2002/2002 [00:00<00:00, 3748.81it/s]


- calc. chi2 A/B-test...


...

100%|██████████| 2002/2002 [00:04<00:00, 405.53it/s]


- calc. AB - Wasserstein...


100%|██████████| 2002/2002 [00:04<00:00, 463.21it/s]


- calc. loss...


 31%|███▏      | 628/2002 [00:04<00:09, 138.89it/s]/home/jovyan/bayesian-ab-test/bayesian_test.py:190: RuntimeWarning:

divide by zero encountered in log

 43%|████▎     | 867/2002 [00:06<00:08, 140.79it/s]/home/jovyan/bayesian-ab-test/bayesian_test.py:189: RuntimeWarning:

divide by zero encountered in log

100%|██████████| 2002/2002 [00:14<00:00, 138.68it/s]
/home/jovyan/bayesian-ab-test/bayesian_test.py:147: RuntimeWarning:

invalid value encountered in divide



In [13]:
df.head(10)

t  n_impr_a1  n_clicks_a1   cost_a1  n_impr_a2  n_clicks_a2   cost_a2  n_impr_b1  n_clicks_b1   cost_b1  n_impr_b2  n_clicks_b2   cost_b2  n_impr_a  n_clicks_a    cost_a  n_impr_b  n_clicks_b    cost_b  acc_impr_a1  acc_cost_a1  acc_clicks_a1  acc_impr_a2  acc_cost_a2  acc_clicks_a2  acc_impr_a  acc_cost_a  acc_clicks_a  acc_impr_b1  acc_cost_b1  acc_clicks_b1  acc_impr_b2  acc_cost_b2  acc_clicks_b2  acc_impr_b  acc_cost_b  acc_clicks_b  chi2_A1A2_ctr  pvalue_A1A2_ctr  chi2_B1B2_ctr  pvalue_B1B2_ctr  chi2_ctr  pvalue_ctr  chi2_A1A2_cpc  pvalue_A1A2_cpc  chi2_B1B2_cpc  pvalue_B1B2_cpc  chi2_cpc  pvalue_cpc  alpha_a1  beta_a1  alpha_a2  beta_a2  alpha_a  beta_a  alpha_b1  beta_b1  alpha_b2  beta_b2  alpha_b  beta_b      a_a1  scale_a1      a_a2  scale_a2       a_a  scale_a      a_b1  scale_b1      a_b2  scale_b2       a_b   scale_b  P_A1A2_b_ks  P_B1B2_b_ks  P_A1A2_b_ws  P_B1B2_b_ws  P_A1A2_g_ks  P_B1B2_g_ks  P_A1A2_g_ws  P_B1B2_g_ws  P_BA_b  P_AB_b  P_BA_g  P_AB_g  P_AB_b_ks  P_AB_g_ks  P_AB_b_ws  P_AB_g_ws  loss_ctr_a  loss_ctr_b  loss_cpc_a  loss_cpc_b
0  0.0          0            0  0.000000          0            0  0.000000          0            0  0.000000          0            0  0.000000         0           0  0.000000         0           0  0.000000            0     0.000000              0            0     0.000000              0           0    0.000000             0            0     0.000000              0            0     0.000000              0           0    0.000000             0       0.000000         1.000000       0.000000         1.000000  0.000000    1.000000            0.0              1.0            0.0              1.0       0.0         1.0         1        1         1        1        1       1         1        1         1        1        1       1  1.000000       inf  1.000000       inf  1.000000      inf  1.000000       inf  1.000000       inf  1.000000       inf        0.964        0.973     1.000000     1.000000          1.0        1.000     1.000000     1.000000   0.531   0.469   0.000   1.000      0.963      1.000   1.000000   1.000000    0.178000    0.164000         NaN         NaN
1  1.0          1            0  0.010583          4            1  0.067957          2            0  0.036128          0            0  0.000000         5           1  0.078540         2           0  0.036128            1     0.010583              0            4     0.067957              1           5    0.078540             1            2     0.036128              0            0     0.000000              0           2    0.036128             0       0.000000         1.000000       0.000000         1.000000  0.000000    1.000000            0.0              1.0            0.0              1.0       0.0         1.0         1        2         2        4        2       5         1        3         1        1        1       3  1.010583       inf  1.067957       1.0  1.078540      1.0  1.036128       inf  1.000000       inf  1.036128       inf        0.880        0.631     0.948411     0.750250          0.0        1.000     0.659817     1.000000   0.427   0.573   1.000   0.000      0.842      0.000   0.952169   0.663968    0.080571    0.127107         NaN         NaN
2  2.0          4            0  0.050797          3            0  0.030781          3            0  0.055435          4            0  0.085070         7           0  0.081579         7           0  0.140506            5     0.061380              0            7     0.098739              1          12    0.160119             1            5     0.091563              0            4     0.085070              0           9    0.176634             0       0.000000         1.000000       0.000000         1.000000  0.000000    1.000000            0.0              1.0            0.0              1.0       0.0         1.0         1        6         2        7        2      12         1        6         1        5        1      10  1.061380       inf  1.098739       1.0  1.16011

## Visualise

#### Analyse specific time period

In [14]:
# Choose specific time period to look at
# T = 950
T = 2000

# Extract dataframe (row) for that time
df_T = df[df.t==T]
df_T

t  n_impr_a1  n_clicks_a1  cost_a1  n_impr_a2  n_clicks_a2   cost_a2  n_impr_b1  n_clicks_b1   cost_b1  n_impr_b2  n_clicks_b2   cost_b2  n_impr_a  n_clicks_a    cost_a  n_impr_b  n_clicks_b    cost_b  acc_impr_a1  acc_cost_a1  acc_clicks_a1  acc_impr_a2  acc_cost_a2  acc_clicks_a2  acc_impr_a  acc_cost_a  acc_clicks_a  acc_impr_b1  acc_cost_b1  acc_clicks_b1  acc_impr_b2  acc_cost_b2  acc_clicks_b2  acc_impr_b  acc_cost_b  acc_clicks_b  chi2_A1A2_ctr  pvalue_A1A2_ctr  chi2_B1B2_ctr  pvalue_B1B2_ctr   chi2_ctr  pvalue_ctr  chi2_A1A2_cpc  pvalue_A1A2_cpc  chi2_B1B2_cpc  pvalue_B1B2_cpc  chi2_cpc  pvalue_cpc  alpha_a1  beta_a1  alpha_a2  beta_a2  alpha_a  beta_a  alpha_b1  beta_b1  alpha_b2  beta_b2  alpha_b  beta_b       a_a1  scale_a1       a_a2  scale_a2        a_a   scale_a       a_b1  scale_b1       a_b2  scale_b2         a_b   scale_b  P_A1A2_b_ks  P_B1B2_b_ks  P_A1A2_b_ws  P_B1B2_b_ws  P_A1A2_g_ks  P_B1B2_g_ks  P_A1A2_g_ws  P_B1B2_g_ws  P_BA_b  P_AB_b  P_BA_g  P_AB_g  P_AB_b_ks  P_AB_g_ks  P_AB_b_ws  P_AB_g_ws  loss_ctr_a  loss_ctr_b  loss_cpc_a  loss_cpc_b
2000  2000.0          0            0      0.0          4            0  0.035138          3            0  0.060384          3            1  0.058458         4           0  0.035138         6           1  0.118841         3932    43.143261            385         3966    43.816488            399        7898   86.959749           784         4030    76.462617            483         3931    74.795787            476        7961  151.258404           959       0.130696         0.717711       0.018416         0.892054  17.972938    0.000022            0.0              1.0            0.0              1.0  7.505453    0.006151       386     3548       400     3568      785    7115       484     3548       477     3456      960    7003  44.143261  0.002597  44.816488  0.002506  87.959749  0.001276  77.462617   0.00207  75.795787  0.002101  152.258404  0.001043        0.741        0.899     0.997315     0.998759        0.937        0.956     0.997667     0.998858     1.0     0.0   0.996   0.004        0.0      0.069   0.978831   0.953472     0.02119         0.0    0.000018    0.046127

In [15]:
# Click-Through-Rate - Beta distribution
print( f'Beta distributions at T:{T} - Impr A: {df_T.acc_impr_a1.values[0]} / {df_T.acc_impr_a2.values[0]} - Impr B: {df_T.acc_impr_b1.values[0]} / {df_T.acc_impr_b2.values[0]}' )
print( f'- Clicks A: {df_T.acc_clicks_a1.values[0]} / {df_T.acc_clicks_a2.values[0]} - Clicks B: {df_T.acc_clicks_b1.values[0]} / {df_T.acc_clicks_b2.values[0]}' )
print( f'- Cost A: {df_T.acc_cost_a1.values[0]:.3f} / {df_T.acc_cost_a2.values[0]:.3f} - Cost B: {df_T.acc_cost_b1.values[0]:.3f} / {df_T.acc_cost_b2.values[0]:.3f}' )

x = np.linspace(0.05, 0.15, 1000)
p_data = [plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a1, df_T.beta_a1), color=0, opacity=0.7, name='A1', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a2, df_T.beta_a2), color=0, opacity=0.7, name='A2', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b1, df_T.beta_b1), color=1, opacity=0.7, name='B1', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b2, df_T.beta_b2), color=1, opacity=0.7, name='B2', showlegend=True)]
layout = plot.layout(title=f'Beta distributions at T:{T}', x_label='Click-Through-Rate', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout)
fig.show()

print( f'Beta distributions at T:{T} - Impr A:{df_T.acc_impr_a.values[0]} - Impr B:{df_T.acc_impr_b.values[0]}' )
p_data = [plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a, df_T.beta_a), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b, df_T.beta_b), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title=f'Beta distributions at T:{T}', x_label='Click-Through-Rate', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

# Cost-per-Click - Gamma distributions
print( f'Beta distributions at T:{T} - Impr A1:{df_T.acc_impr_a1.values[0]} - Impr A1:{df_T.acc_impr_a2.values[0]} - Impr B1:{df_T.acc_impr_b1.values[0]} - Impr B2:{df_T.acc_impr_b2.values[0]}' )
x = np.linspace(0, 0.3, 1000)
p_data = [plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a1, scale=df_T.scale_a1), color=0, opacity=0.7, name='A1', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a2, scale=df_T.scale_a2), color=0, opacity=0.7, name='A2', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b1, scale=df_T.scale_b1), color=1, opacity=0.7, name='B1', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b2, scale=df_T.scale_b2), color=1, opacity=0.7, name='B2', showlegend=True)]
layout = plot.layout(title=f'Gamma distributions at T:{T} - Impr A:{df_T.acc_impr_a1.values[0]} - Impr B:{df_T.acc_impr_a2.values[0]}', x_label='Cost-per-Click', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout)
fig.show()

p_data = [plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a, scale=df_T.scale_a), color=0, opacity=0.7, name='A', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b, scale=df_T.scale_b), color=1, opacity=0.7, name='B', showlegend=True)]
layout = plot.layout(title=f'Gamma distributions at T:{T} - Cost A:{df_T.acc_cost_a.values[0]:.3f} - Cost B:{df_T.acc_cost_b.values[0]:.3f}', x_label='Cost-per-Click', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()

Beta distributions at T:2000 - Impr A: 3932 / 3966 - Impr B: 4030 / 3931
- Clicks A: 385 / 399 - Clicks B: 483 / 476
- Cost A: 43.143 / 43.816 - Cost B: 76.463 / 74.796


Beta distributions at T:2000 - Impr A:7898 - Impr B:7961


Beta distributions at T:2000 - Impr A1:3932 - Impr A1:3966 - Impr B1:4030 - Impr B2:3931


<hr>

# DECISION TIME

In [16]:
# Select last event to evaluate 
# T = len(df)-2
T = 1000

df_T = df[df.t==T]
df_T

t  n_impr_a1  n_clicks_a1   cost_a1  n_impr_a2  n_clicks_a2   cost_a2  n_impr_b1  n_clicks_b1   cost_b1  n_impr_b2  n_clicks_b2   cost_b2  n_impr_a  n_clicks_a    cost_a  n_impr_b  n_clicks_b    cost_b  acc_impr_a1  acc_cost_a1  acc_clicks_a1  acc_impr_a2  acc_cost_a2  acc_clicks_a2  acc_impr_a  acc_cost_a  acc_clicks_a  acc_impr_b1  acc_cost_b1  acc_clicks_b1  acc_impr_b2  acc_cost_b2  acc_clicks_b2  acc_impr_b  acc_cost_b  acc_clicks_b  chi2_A1A2_ctr  pvalue_A1A2_ctr  chi2_B1B2_ctr  pvalue_B1B2_ctr  chi2_ctr  pvalue_ctr  chi2_A1A2_cpc  pvalue_A1A2_cpc  chi2_B1B2_cpc  pvalue_B1B2_cpc  chi2_cpc  pvalue_cpc  alpha_a1  beta_a1  alpha_a2  beta_a2  alpha_a  beta_a  alpha_b1  beta_b1  alpha_b2  beta_b2  alpha_b  beta_b       a_a1  scale_a1       a_a2  scale_a2        a_a   scale_a       a_b1  scale_b1       a_b2  scale_b2       a_b   scale_b  P_A1A2_b_ks  P_B1B2_b_ks  P_A1A2_b_ws  P_B1B2_b_ws  P_A1A2_g_ks  P_B1B2_g_ks  P_A1A2_g_ws  P_B1B2_g_ws  P_BA_b  P_AB_b  P_BA_g  P_AB_g  P_AB_b_ks  P_AB_g_ks  P_AB_b_ws  P_AB_g_ws  loss_ctr_a  loss_ctr_b  loss_cpc_a  loss_cpc_b
1000  1000.0          4            0  0.047748          2            1  0.029568          2            1  0.036983          3            0  0.061563         6           1  0.077316         5           1  0.098545         1929    21.220762            187         1978    21.951046            206        3907   43.171808           393         2083    39.569956            244         1988    37.808434            240        4071    77.37839           484       0.479741          0.48854       0.093663         0.759571  6.619172    0.010089       0.004664         0.945554       0.000185         0.989149  4.045195    0.044297       188     1743       207     1773      394    3515       245     1840       241     1749      485    3588  22.220762  0.005348  22.951046  0.004854  44.171808  0.002545  40.569956  0.004098  38.808434  0.004167  78.37839  0.002066        0.593        0.756     0.992821     0.996404        0.858        0.927     0.992593     0.995436   0.994   0.006   0.979   0.021      0.057      0.153   0.981734   0.950507    0.018412    0.000266    0.000208    0.049255

In [17]:
# Analysis
print(f'A: Impr: {df_T.acc_impr_a.values[0]} - Clicks: {df_T.acc_clicks_a.values[0]}')
print(f'B: Impr: {df_T.acc_impr_b.values[0]} - Clicks: {df_T.acc_clicks_b.values[0]}')

A: Impr: 3907 - Clicks: 393
B: Impr: 4071 - Clicks: 484


## A/A test

In [18]:
# Same/Same statistical test
print(f'A/A TEST - CTR')
print(f'AA: chi2: {df_T.chi2_A1A2_ctr.values[0]:.3f} - p-value: {100*df_T.pvalue_A1A2_ctr.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_A1A2_b_ks.values[0]:.3f}', end='') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_A1A2_b_ws.values[0]:.3f}', end='') if config['metrics']['ws'] else None
print('')
print(f'BB: chi2: {df_T.chi2_B1B2_ctr.values[0]:.3f} - p-value: {100*df_T.pvalue_B1B2_ctr.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_B1B2_b_ks.values[0]:.3f}', end='') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_B1B2_b_ws.values[0]:.3f}', end='') if config['metrics']['ws'] else None
print(f'\n')

print(f'A/A TEST - CpC')
print(f'AA: chi2: {df_T.chi2_A1A2_cpc.values[0]:.3f} - p-value: {100*df_T.pvalue_A1A2_cpc.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_A1A2_g_ks.values[0]:.3f}') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_A1A2_g_ws.values[0]:.3f}') if config['metrics']['ws'] else None
print(f'BB: chi2: {df_T.chi2_B1B2_cpc.values[0]:.3f} - p-value: {100*df_T.pvalue_B1B2_cpc.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_B1B2_g_ks.values[0]:.3f}') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_B1B2_g_ws.values[0]:.3f}') if config['metrics']['ws'] else None

A/A TEST - CTR
AA: chi2: 0.480 - p-value: 48.9% - ks: 0.593 - ws: 0.993
BB: chi2: 0.094 - p-value: 76.0% - ks: 0.756 - ws: 0.996

A/A TEST - CpC
AA: chi2: 0.005 - p-value: 94.6% - ks: 0.858
 - ws: 0.993
BB: chi2: 0.000 - p-value: 98.9% - ks: 0.927
 - ws: 0.995


#### Hypothesis testing - Chi2-test

In [19]:
# CHI2-Test - CTR
p_data = [ plot.plot(x=df.acc_impr_a, y=df.pvalue_A1A2_ctr, color=0, opacity=0.7, name='p-value A1=A2', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.pvalue_B1B2_ctr, color=1, opacity=0.7, name='p-value B1=B2', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.pvalue_ctr, color=3, opacity=0.7, name='p-value A=B', showlegend=True),
           plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.95], color=0, opacity=1, fill=None, linewidth=3, name='>0.95', showlegend=True),
           ]
layout = plot.layout(title=f'Chi2 test - p-value of A/A (CTR)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AA-test_chi2_ctr.png')

# CHI2-Test - CpC
p_data = [ plot.plot(x=df.acc_impr_a, y=df.pvalue_A1A2_cpc, color=0, opacity=0.7, name='p-value A1=A2', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.pvalue_B1B2_cpc, color=1, opacity=0.7, name='p-value B1=B2', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.pvalue_cpc, color=3, opacity=0.7, name='p-value A=B', showlegend=True),
           plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.95], color=0, opacity=1, fill=None, linewidth=3, name='>0.95', showlegend=True),
           ]
layout = plot.layout(title=f'Chi2 test - p-value of A/A (CpC)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AA-test_chi2_cpc.png')

#### Bayesian A/A testing

In [20]:
# Click-Through-Rate
x = np.linspace(0.05, 0.15, 1000)
p_data = [plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a1, df_T.beta_a1), color=0, opacity=0.7, name='A1', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a2, df_T.beta_a2), color=0, opacity=0.7, name='A2', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b1, df_T.beta_b1), color=1, opacity=0.7, name='B1', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b2, df_T.beta_b2), color=1, opacity=0.7, name='B2', showlegend=True)]
layout = plot.layout(title=f'Beta distributions at T:{T}', x_label='engagement rate', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AA-test_betas.png')

# Kolmogorov-Smirnov plot
if config['metrics']['ks']:
    p_data = [ plot.plot(x=df.acc_impr_a, y=df.P_A1A2_b_ks, color=0, opacity=0.5, name='P(A1=A2)', showlegend=True),
            plot.plot(x=df.acc_impr_b, y=df.P_B1B2_b_ks, color=1, opacity=0.5, name='P(B1=B2)', showlegend=True),
            plot.plot(x=df.acc_impr_a, y=df.P_AB_b_ks, color=3, opacity=0.9, name='P(AB)', showlegend=True)]
    layout = plot.layout(title=f'Kolmogorov-Smirnov A/A (CTR)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
    fig = go.Figure(data=p_data, layout=layout).show()
    layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
    go.Figure(data=p_data, layout=layout).write_image('images/AA-test_CTR_ks.png')

# Wasserstein plot
if config['metrics']['ws']:
    p_data = [ plot.plot(x=df.acc_impr_a, y=df.P_A1A2_b_ws, color=0, opacity=0.5, name='P(A1=A2)', showlegend=True),
            plot.plot(x=df.acc_impr_b, y=df.P_B1B2_b_ws, color=1, opacity=0.5, name='P(B1=B2)', showlegend=True),
            plot.plot(x=df.acc_impr_a, y=df.P_AB_b_ws, color=3, opacity=0.9, name='P(AB)', showlegend=True)]
    layout = plot.layout(title=f'Wasserstein A/A (CTR)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
    layout['yaxis']['range'] = [0.95, 1]
    fig = go.Figure(data=p_data, layout=layout).show()
    layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
    go.Figure(data=p_data, layout=layout).write_image('images/AA-test_CTR_ws.png')

In [21]:
# Cost-per-Click
x = np.linspace(0, 0.3, 1000)
p_data = [plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a1, scale=df_T.scale_a1), color=0, opacity=0.7, name='A1', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a2, scale=df_T.scale_a2), color=0, opacity=0.7, name='A2', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b1, scale=df_T.scale_b1), color=1, opacity=0.7, name='B1', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b2, scale=df_T.scale_b2), color=1, opacity=0.7, name='B2', showlegend=True)]
layout = plot.layout(title=f'Gamma distributions at T:{T}', x_label='Cost-per-Click', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AA-test_CpC_gamma.png')

# Kolmogorov-Smirnov plot
if config['metrics']['ks']:
        p_data = [ plot.plot(x=df.acc_impr_a, y=df.P_A1A2_g_ks, color=0, opacity=0.5, name='P(A1=A2)', showlegend=True),
                plot.plot(x=df.acc_impr_b, y=df.P_B1B2_g_ks, color=1, opacity=0.5, name='P(B1=B2)', showlegend=True),
                plot.plot(x=df.acc_impr_a, y=df.P_AB_g_ks, color=3, opacity=0.9, name='P(AB)', showlegend=True)]
        layout = plot.layout(title=f'Kolmogorov-Smirnov A/A (CpC)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
        fig = go.Figure(data=p_data, layout=layout).show()
        layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
        go.Figure(data=p_data, layout=layout).write_image('images/AA-test_CpC_ks.png')

if config['metrics']['ws']:
    p_data = [ plot.plot(x=df.acc_impr_a, y=df.P_A1A2_g_ws, color=0, opacity=0.5, name='P(A1=A2)', showlegend=True),
               plot.plot(x=df.acc_impr_b, y=df.P_B1B2_g_ws, color=1, opacity=0.5, name='P(B1=B2)', showlegend=True),
               plot.plot(x=df.acc_impr_a, y=df.P_AB_g_ws, color=3, opacity=0.9, name='P(AB)', showlegend=True)]
    layout = plot.layout(title=f'Wasserstein A/A (CpC)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
    layout['yaxis']['range'] = [0.95, 1]
    fig = go.Figure(data=p_data, layout=layout).show()
    layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
    go.Figure(data=p_data, layout=layout).write_image('images/AA-test_CpC_ws.png')

## A/B-Test - Decision Probability

In [22]:
print(f'DECISION METRICS - AB')
print(f'A: Impr: {df_T.acc_impr_a.values[0]} - Clicks: {df_T.acc_clicks_a.values[0]} - Cost: {df_T.acc_cost_a.values[0]:.2f}')
print(f'B: Impr: {df_T.acc_impr_b.values[0]} - Clicks: {df_T.acc_clicks_b.values[0]} - Cost: {df_T.acc_cost_b.values[0]:.2f}\n')

# Decision metrics
print(f'DECISION METRICS - AB - CTR')
print(f'chi2: {df_T.chi2_ctr.values[0]:.3f} - p-value: {100*df_T.pvalue_ctr.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_AB_b_ks.values[0]:.3f}', end='') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_AB_b_ws.values[0]:.3f}', end='') if config['metrics']['ws'] else None
print('')
print(f'CTR: P(A>B): {100*df_T.P_AB_b.values[0]:.1f}% / {100*df_T.P_BA_b.values[0]:.1f}% - loss (A/B): {df_T.loss_ctr_a.values[0]:.5f} / {df_T.loss_ctr_b.values[0]:.5f}\n')

print(f'DECISION METRICS - AB - CpC')
# print(f'chi2: {df_T.chi2_cpc.values[0]:.3f} - p-value: {100*df_T.pvalue_cpc.values[0]:.1f}%  --  ks: {df_T.P_AB_g_ks.values[0]:.3f} - ws: {df_T.P_AB_g_ws.values[0]:.3f}')
print(f'chi2: {df_T.chi2_cpc.values[0]:.3f} - p-value: {100*df_T.pvalue_cpc.values[0]:.1f}%', end='')
print(f' - ks: {df_T.P_AB_g_ks.values[0]:.3f}', end='') if config['metrics']['ks'] else None
print(f' - ws: {df_T.P_AB_g_ws.values[0]:.3f}', end='') if config['metrics']['ws'] else None
print('')
print(f'CpC p(A>B) {100*df_T.P_AB_g.values[0]:.1f}% / {100*df_T.P_BA_g.values[0]:.1f}% - loss (A/B): {df_T.loss_cpc_a.values[0]:.5f} / {df_T.loss_cpc_b.values[0]:.5f}')

DECISION METRICS - AB
A: Impr: 3907 - Clicks: 393 - Cost: 43.17
B: Impr: 4071 - Clicks: 484 - Cost: 77.38

DECISION METRICS - AB - CTR
chi2: 6.619 - p-value: 1.0% - ks: 0.057 - ws: 0.982
CTR: P(A>B): 0.6% / 99.4% - loss (A/B): 0.01841 / 0.00027

DECISION METRICS - AB - CpC
chi2: 4.045 - p-value: 4.4% - ks: 0.153 - ws: 0.951
CpC p(A>B) 2.1% / 97.9% - loss (A/B): 0.00021 / 0.04926


#### Hypothesis testing

In [23]:
# CHI2 - CTR
p_data = [ plot.plot(x=df.acc_impr_b, y=df.pvalue_ctr, color=1, opacity=0.7, name='p-value', showlegend=True),
           plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.05], color=0, opacity=1, fill=None, linewidth=3, name='<0.05', showlegend=True),
           ]
layout = plot.layout(title=f'Chi2-test - p-value (CTR)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_chi2_pvalue_ctr.png')

# CHI2 - CpC
p_data = [ plot.plot(x=df.acc_impr_b, y=df.pvalue_cpc, color=1, opacity=0.7, name='p-value', showlegend=True),
           plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.05], color=0, opacity=1, fill=None, linewidth=3, name='<0.05', showlegend=True),
           ]
layout = plot.layout(title=f'Chi2-test - p-value (CpC)', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_chi2_pvalue_cpc.png')

#### Bayesian testing

In [24]:

x = np.linspace(0.05, 0.15, 1001)
p_data = [plot.plot(x=x, y=beta.pdf(x, df_T.alpha_a, df_T.beta_a), color=0, opacity=0.7, name='CTR A', showlegend=True),
          plot.plot(x=x, y=beta.pdf(x, df_T.alpha_b, df_T.beta_b), color=1, opacity=0.7, name='CTR B', showlegend=True)]
layout = plot.layout(title=f'Performance distributions at T:{T}', x_label='engagement rate', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CTR_betas.png')

x = np.linspace(0, 0.3, 1001)
p_data = [plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_a, scale=df_T.scale_a), color=0, opacity=0.7, name='CpC A', showlegend=True),
          plot.plot(x=x, y=gamma.pdf(x, a=df_T.a_b, scale=df_T.scale_b), color=1, opacity=0.7, name='CpC B', showlegend=True)]
layout = plot.layout(title=f'Performance distributions at T:{T}', x_label='engagement rate', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CpC_gammas.png')


# BAYES - CTR
p_data = [ plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.95], color=0, opacity=1, fill=None, linewidth=3, name='>0.95', showlegend=True),
           plot.plot(x=df.acc_impr_a, y=df.P_AB_b, color=0, opacity=0.7, name='P(A>B)', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.P_BA_b, color=1, opacity=0.7, name='P(B>A)', showlegend=True),
           ]
layout = plot.layout(title=f'Probability of P(B>A), P(A>B) - CTR', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CTR_prob.png')

p_data = [ plot.plot(x=df.acc_impr_a, y=df.loss_ctr_a, color=0, opacity=0.5, name='loss A', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.loss_ctr_b, color=1, opacity=0.8, name='loss B', showlegend=True),
           ]
layout = plot.layout(title=f'Loss - CTR', x_label='# impressions', y_label='loss', theme='dark', width=1200, height=400)
layout['yaxis']['range'] = [0, 0.05]
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CTR_loss.png')

# BAYES - CpC
p_data = [ plot.plot(x=list(range(n_impressions_a)), y=n_impressions_a*[0.95], color=0, opacity=1, fill=None, linewidth=3, name='>0.95', showlegend=True),
           plot.plot(x=df.acc_impr_a, y=df.P_AB_g, color=0, opacity=0.7, name='P(B<A)', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.P_BA_g, color=1, opacity=0.7, name='P(A<B)', showlegend=True),
           ]
layout = plot.layout(title=f'Probability of P(A<B), P(B<A) - CpC', x_label='# impressions', y_label='p', theme='dark', width=1200, height=400)
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CpC_prob.png')

p_data = [ plot.plot(x=df.acc_impr_a, y=df.loss_cpc_a, color=0, opacity=0.5, name='loss A', showlegend=True),
           plot.plot(x=df.acc_impr_b, y=df.loss_cpc_b, color=1, opacity=0.8, name='loss B', showlegend=True),
           ]
layout = plot.layout(title=f'Loss - CpC', x_label='# impressions', y_label='loss', theme='dark', width=1200, height=400)
# layout['yaxis']['range'] = [0, 0.05]
fig = go.Figure(data=p_data, layout=layout).show()
layout['width'], layout['height'] = WIDTH_SAVE, HEIGHT_SAVE
go.Figure(data=p_data, layout=layout).write_image('images/AB-test_CpC_loss.png')

### Video

In [25]:
if True:

    N_STEPS = 500
    x = np.linspace(0, 0.5, 50000)

    def make_video(framerate=10, xlabel='', n_versions=4, colormap=['#ff4444', '#ff4444', '#ff44ff', '#ff44ff'], txt_pos=0.4):
        FFMpegWriter = manimation.writers['ffmpeg']
        metadata = dict(title='Movie Test', artist='Matplotlib', comment='')
        writer = FFMpegWriter(fps=framerate, metadata=metadata)

        # fig = plt.figure
        fig = plt.figure(figsize=(12,6), dpi=100, facecolor='#202020', edgecolor='#202020')
        plt.margins(10)

        ax = plt.gca()
        fig.patch.set_facecolor('#202020')
        ax.set_facecolor('#202020')
        ax.set_xlabel(xlabel)
        ax.set_ylabel('#')
        ax.spines['bottom'].set_color('#AAAAAA')
        ax.spines['top'].set_color('#AAAAAA')
        ax.spines['left'].set_color('#AAAAAA')
        ax.spines['right'].set_color('#AAAAAA')
        ax.xaxis.label.set_color('#AAAAAA')
        ax.tick_params(axis='x', colors='#AAAAAA')

        # colorsteps = math.floor(255/n_versions)
        # colormap = [rgb2hex(np.array([255,colorsteps*i,colorsteps*i])/255) for i in range(n_versions)]
        plts = [plt.plot([], [], colormap[i], linewidth=3)[0] for i in range(n_versions)]
        plt.xlim([0, 0.25])
        plt.ylim([0, 100])
        txt_time = plt.figtext(0.7, txt_pos, "", fontsize=12, color='#AAAAAA')
        ax.get_yaxis().set_visible(False)

        return writer, fig, plt, plts, txt_time


    # A/A-test - on campaign CTR data...
    writer, fig, plt, plts, txt_time = make_video(xlabel='Click-Through-Rate (AA-test)', txt_pos=0.35)
    with writer.saving(fig, 'video/AA-test_CTR.mp4', 100):
        for t in tqdm(range(N_STEPS+1)):
            plts[0].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_a1'], df.loc[t,'beta_a1']))
            plts[1].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_a2'], df.loc[t,'beta_a2']))
            plts[2].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_b1'], df.loc[t,'beta_b1']))
            plts[3].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_b2'], df.loc[t,'beta_b2']))
            
            txt = ' time: {}\n\n A1 / A2\n impr.: {} / {}\n clicks: {} / {}\n'.format(t, df.loc[t,'acc_impr_a1'], df.loc[t,'acc_impr_a2'], df.loc[t,'acc_clicks_a1'], df.loc[t,'acc_clicks_a2'])
            txt += ' ks: {:.3f} '.format(df.loc[t,'P_A1A2_b_ks']) if config['metrics']['ks'] else ''
            txt += ' ws: {:.3f} '.format(df.loc[t,'P_A1A2_b_ws']) if config['metrics']['ws'] else ''
            txt += '\n\n'
            txt += ' B1 / B2\n impr.: {} / {}\n clicks: {} / {}\n'.format(df.loc[t,'acc_impr_b1'], df.loc[t,'acc_impr_b2'], df.loc[t,'acc_clicks_b1'], df.loc[t,'acc_clicks_b2'])
            txt += ' ks: {:.3f} '.format(df.loc[t,'P_B1B2_b_ks']) if config['metrics']['ks'] else ''
            txt += ' ws: {:.3f}'.format(df.loc[t,'P_B1B2_b_ws']) if config['metrics']['ws'] else ''
            txt_time.set_text(txt)
            writer.grab_frame(facecolor=fig.get_facecolor(), edgecolor='none')
    plt.close()

    # A/A-test - on campaign CpC data...
    writer, fig, plt, plts, txt_time = make_video(xlabel='Cost-per-Click (AA-test)', txt_pos=0.35)
    plt.xlim([0, 0.5])
    plt.ylim([0, 20])
    with writer.saving(fig, 'video/AA-test_CpC.mp4', 100):
        for t in tqdm(range(N_STEPS+1)):
            plts[0].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_a1'], scale=df.loc[t,'scale_a1']))
            plts[1].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_a2'], scale=df.loc[t,'scale_a2']))
            plts[2].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_b1'], scale=df.loc[t,'scale_b1']))
            plts[3].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_b2'], scale=df.loc[t,'scale_b2']))
            
            txt = ' time: {}\n\n A1 / A2\n clicks.: {} / {}\n cost: {:.2f} / {:.2f}\n'.format(t, df.loc[t,'acc_clicks_a1'], df.loc[t,'acc_clicks_a2'], df.loc[t,'acc_cost_a1'], df.loc[t,'acc_cost_a2'])
            txt += ' ks: {:.3f}'.format(df.loc[t,'P_A1A2_g_ks']) if config['metrics']['ks'] else ''
            txt += ' ws: {:.3f}'.format(df.loc[t,'P_A1A2_g_ws']) if config['metrics']['ws'] else ''
            txt += '\n\n'
            txt += ' B1 / B2\n clicks.: {} / {}\n cost: {:.2f} / {:.2f}\n'.format(df.loc[t,'acc_clicks_b1'], df.loc[t,'acc_clicks_b2'], df.loc[t,'acc_cost_b1'], df.loc[t,'acc_cost_b2'])
            txt += ' ks: {:.3f}'.format(df.loc[t,'P_B1B2_g_ks']) if config['metrics']['ks'] else ''
            txt += ' ws: {:.3f}'.format(df.loc[t,'P_B1B2_g_ws']) if config['metrics']['ws'] else ''
            txt_time.set_text(txt)
            writer.grab_frame(facecolor=fig.get_facecolor(), edgecolor='none')
    plt.close()


    # A/B-test - on campaign CTR data...
    writer, fig, plt, plts, txt_time = make_video(xlabel='Click-Through-Rate (AB-test)', n_versions=2, colormap=['#ff4444','#ff44ff'], txt_pos=0.4)
    plt.ylim([0, 70])
    with writer.saving(fig, 'video/AB-test_CTR.mp4', 100):
        for t in tqdm(range(N_STEPS+1)):
            plts[0].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_a'], df.loc[t,'beta_a']))
            plts[1].set_data(x, stats.beta.pdf(x, df.loc[t,'alpha_b'], df.loc[t,'beta_b']))

            txt = ' time: {}\n\n A / B\n impr.: {} / {}\n clicks: {} / {}\n\n'.format(t, df.loc[t,'acc_impr_a'], df.loc[t,'acc_impr_b'], df.loc[t,'acc_clicks_a'], df.loc[t,'acc_clicks_b'])
            txt += ' p-value: {:.1f}%\n\n'.format(100*df.loc[t,'pvalue_ctr'])
            txt += ' p(a>b): {:.1f}% / {:.1f}%\n'.format(100*df.loc[t,'P_AB_b'], 100*df.loc[t,'P_BA_b'])
            txt += ' loss: {:.3f} / {:.3f} \n\n'.format(df.loc[t,'loss_ctr_a'], df.loc[t,'loss_ctr_b'])
            txt_time.set_text(txt)

            # txt_time.set_text( " time: {}\n\n impr.: {}\n clicks: {}".format(t, df.loc[t,'acc_impr_a']+df.loc[t,'acc_impr_b'], df.loc[t,'acc_clicks_a']+df.loc[t,'acc_clicks_b']))
            writer.grab_frame(facecolor=fig.get_facecolor(), edgecolor='none')
    plt.close()


    # A/B-test - on campaign CpC data...
    writer, fig, plt, plts, txt_time = make_video(xlabel='Cost-per-Click (AB-test)', n_versions=2, colormap=['#ff4444','#ff44ff'], txt_pos=0.4)
    plt.xlim([0, 0.5])
    plt.ylim([0, 20])
    with writer.saving(fig, 'video/AB-test_CpC.mp4', 100):
        for t in tqdm(range(N_STEPS+1)):
            plts[0].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_a'], scale=df.loc[t,'scale_a']))
            plts[1].set_data(x, stats.gamma.pdf(x, a=df.loc[t,'a_b'], scale=df.loc[t,'scale_b']))
            
            txt = ' time: {}\n\n A / B\n clicks: {} / {}\n cost: {:.2f} / {:.2f}\n\n'.format(t, df.loc[t,'acc_clicks_a'], df.loc[t,'acc_clicks_b'], df.loc[t,'acc_cost_a'], df.loc[t,'acc_cost_b'])
            txt += ' p-value: {:.1f}%\n\n'.format(100*df.loc[t,'pvalue_cpc'])
            txt += ' p(a<b): {:.1f}% / {:.1f}%\n'.format(100*(1-df.loc[t,'P_AB_g']), 100*(1-df.loc[t,'P_BA_g']))
            txt += ' loss: {:.3f} / {:.3f} \n\n'.format(df.loc[t,'loss_cpc_a'], df.loc[t,'loss_cpc_b'])
            txt_time.set_text(txt)
            
            writer.grab_frame(facecolor=fig.get_facecolor(), edgecolor='none')
    plt.close()

100%|██████████| 501/501 [00:31<00:00, 15.73it/s]


(0.0, 0.5)

(0.0, 20.0)

100%|██████████| 501/501 [00:26<00:00, 18.92it/s]


(0.0, 70.0)

100%|██████████| 501/501 [00:21<00:00, 23.53it/s]


(0.0, 0.5)

(0.0, 20.0)

100%|██████████| 501/501 [00:19<00:00, 26.08it/s]
